# Predicting Future Stock Prices

In [1]:
import pandas as pd
import numpy as np
from datetime import datetime
import yfinance as yf
import sqlalchemy
import time
import plotly.express as px
import re
import logging 
from prophet import Prophet
from prophet.diagnostics import cross_validation, performance_metrics
from prophet.plot import plot_plotly, plot_components_plotly, add_changepoints_to_plot, plot_cross_validation_metric
logger = logging.getLogger(__name__)
from sklearn.metrics import mean_absolute_percentage_error
from sklearn.metrics import mean_absolute_error
from dask.distributed import Client
import itertools
from StockExplore import ExploreStocks

from plotly.offline import init_notebook_mode, iplot
init_notebook_mode(connected=True)  

### Instantiate Class

In [2]:
#test function
stocks = ExploreStocks(['IAG.L', '0293.HK', 'AF.PA'], '25y')

[*********************100%***********************]  3 of 3 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed
[*********************100%***********************]  1 of 1 completed

% of NaN values in calculated GBP column : 0.01
Data Retrieved - access via the stock_history attribute 


/Users/JacobMennell/PycharmProjects/yahooFinanceAirlineStocks/python-class-analysis_project/StockExplore.py:133: FutureWarning:

Series.dt.weekofyear and Series.dt.week have been deprecated.  Please use Series.dt.isocalendar().week instead.



## Stock analysis

In [ ]:
#plot stock price over time
stocks.plot_stock_price()

In [ ]:
#plot trade volumne over time
stocks.plot_trade_volume()

In [ ]:
#plot stock volatility
stocks.plot_volatility()

In [3]:
#plot rolling average
stocks.plot_rolling_average()

In [ ]:
#plot cumulative return over time
stocks.plot_cumulative_returns()

## Prediction

In [ ]:
#IAG.L
stocks.plot_future_trend('IAG.L', start_date = '2021-04-01', periods = 90, cap=800)

In [ ]:
#0293.HK
stocks.plot_future_trend('0293.HK', start_date = '2021-04-01', periods = 90, cap=30)

In [ ]:
#AF.PA
stocks.plot_future_trend('AF.PA', start_date = '2021-04-01', periods = 90, cap=20)

## Investigate prediction at greater granularity - Model 1B

In [ ]:
#get df from class
df=stocks.stock_history

start_date = '2021-04-01'
growth = 'logistic'
cap = 500
floor = 0
periods = 90
country_name= 'US'
changepoints = True
trend = True
stock = 'IAG.L'

post_date_df = df.loc[~(df['Date'] <= start_date)]
predict_df = post_date_df.loc[post_date_df['Ticker'].isin([stock])]
        
#rename columns to fit model
df = predict_df.rename(columns={'Date': 'ds', 'Close': 'y'})
df = df[['ds', 'y']]
df['cap'] = cap
df['floor'] = floor

#changepoint_prior_scale and seasonality_prior_scale obtained form hypertuning see below
m = Prophet(yearly_seasonality=True, 
            growth=growth,  
            interval_width=0.95, 
            changepoint_prior_scale=0.01, 
            seasonality_prior_scale=0.1)

#get currency code for stock
currency_code = predict_df['currency_code'].values[0]
        
#HOLIDAYS - default is US
if currency_code == 'GBP':
    m.add_country_holidays(country_name = "GB")
elif currency_code == 'HKD':
    m.add_country_holidays(country_name = "HK")
else: 
    m.add_country_holidays(country_name = country_name)
        
m.fit(df)

future = m.make_future_dataframe(periods)
        
# Eliminate weekend from future dataframe
future['day'] = future['ds'].dt.weekday
future = future[future['day']<=4]

future['cap'] = cap
future['floor'] = floor

forecast = m.predict(future)

#format graph
fig = plot_plotly(m, forecast, trend=trend, changepoints=changepoints)
fig.update_layout(title=f'{stock} {periods} days forecast')
output = fig.show()

#get Mean Absolute Error
df_merge = pd.merge(df, forecast[['ds','yhat_lower','yhat_upper','yhat']],on='ds')
df_merge = df_merge[['ds','yhat_lower','yhat_upper','yhat','y']]
# calculate MAE between observed and predicted values 
y_true = df_merge['y'].values
y_pred = df_merge['yhat'].values
mae = mean_absolute_error(y_true, y_pred)
mape = mean_absolute_percentage_error(y_true, y_pred)

print(f'The Mean Absolute Eror is: {"{:.2f}".format(mae)} \nThe Mean Absolute Percentage Eror is: {"{:.2f}".format(mape)} ')

output

In [ ]:
#plot seasonality components
plot_components_plotly(m, forecast)

### Cross Validation to Evaluate Model

In [ ]:
client = Client()  # connect to the cluster - use dash to paralleize cross-validation to speed up

df_cv = cross_validation(m, initial='200 days',
                         period='30 days', 
                         horizon='90 days',
                         parallel="dask")

df_cv.head()

In [ ]:
df_p = performance_metrics(df_cv)
fig = plot_cross_validation_metric(df_cv, metric='mape')

### Explore hypertuning of model parameters - Fed into the above model 1B

In [ ]:
param_grid = {  
    'changepoint_prior_scale': [0.001, 0.01, 0.1, 0.5],
    'seasonality_prior_scale': [0.01, 0.1, 1.0, 10.0],
}

# Generate all combinations of parameters
all_params = [dict(zip(param_grid.keys(), v)) for v in itertools.product(*param_grid.values())]
rmses = []  # Store the RMSEs for each params here

# Use cross validation to evaluate all parameters
for params in all_params:
    m = Prophet(**params).fit(df)  # Fit model with given params
    df_cv = cross_validation(m, horizon='90 days', parallel="dask")
    df_p = performance_metrics(df_cv, rolling_window=1)
    rmses.append(df_p['rmse'].values[0])

# Find the best parameters
tuning_results = pd.DataFrame(all_params)
tuning_results['rmse'] = rmses
print(tuning_results)